In [1]:
import pandas as pd
import numpy as np
import re
import string

In [2]:
df = pd.read_csv('Data/library_json_title_database_use.csv', sep='\t')
df.head()

titleId                                          workTitle  \
0        2  Komplex, Archetypus, Symbol in der Psychologie...   
1  5242885  Hexen- und Dämonenglaube im Lande Braunschweig...   
2  5505056  Qualitative strategies for ethnocultural resea...   
3  2228271                          art of persuading people,   
4  5505076                         Trauma and organizations /   

                                            subjects publicationDate  \
0  Jung, C. G. (Carl Gustav), 1875-1961, Psychoan...            1959   
1  Witchcraft -- Germany -- Braunschweig Region, ...           ©1997   
2  Psychology -- Qualitative research, Ethnology ...           ©2012   
3                       Selling, Psychology, Applied            1938   
4  Associations, institutions, etc, Stress (Psych...            2012   

                                               notes  \
0                      General Note: Includes index.   
1                                               None   
2  Choice Review: This is an important book edite...   
3                     General Note: "First edition."   
4  Summary: This collection of new contributions ...   

                                           thumbnail                 holdings  
0  https://files.lib.byu.edu/search/thumbnails/ca...        BF 174 .J85 J2936  
1                                               None        BF 1583 .L44 1997  
2  https://www.syndetics.com/index.php?isbn=97814...       BF 76.5 .Q355 2012  
3                                               None               BF 636 .W6  
4  https://www.syndetics.com/index.php?isbn=97818...  BF 175.5 .P75 T73x 2012

In [3]:
df = pd.read_csv('Data/library_json_full.csv', sep='\t')
df.head()

titleId                                          fullTitle  \
0        2  Complex, archetype, symbol in the psychology o...   
1  5242885  Hexen- und Dämonenglaube im Lande Braunschweig...   
2  5505056  Qualitative strategies for ethnocultural resea...   
3  2228271  The art of persuading people, by James A. Wors...   
4  5505076  Trauma and organizations / edited by Earl Hopper.   

                                            subjects publicationDate  \
0  Jung, C. G. (Carl Gustav), 1875-1961, Psychoan...            1959   
1  Witchcraft -- Germany -- Braunschweig Region, ...           ©1997   
2  Psychology -- Qualitative research, Ethnology ...           ©2012   
3                       Selling, Psychology, Applied            1938   
4  Associations, institutions, etc, Stress (Psych...            2012   

                                               notes  \
0                      General Note: Includes index.   
1                                               None   
2  Choice Review: This is an important book edite...   
3                     General Note: "First edition."   
4  Summary: This collection of new contributions ...   

                                           thumbnail                 holdings  
0  https://files.lib.byu.edu/search/thumbnails/ca...        BF 174 .J85 J2936  
1                                               None        BF 1583 .L44 1997  
2  https://www.syndetics.com/index.php?isbn=97814...       BF 76.5 .Q355 2012  
3                                               None               BF 636 .W6  
4  https://www.syndetics.com/index.php?isbn=97818...  BF 175.5 .P75 T73x 2012

In [4]:
df = df.drop(['subjects', 'publicationDate', 'notes'], axis=1)
df = df.rename(columns={'holdings':'Call_Number'})
df.head()

titleId                                          fullTitle  \
0        2  Complex, archetype, symbol in the psychology o...   
1  5242885  Hexen- und Dämonenglaube im Lande Braunschweig...   
2  5505056  Qualitative strategies for ethnocultural resea...   
3  2228271  The art of persuading people, by James A. Wors...   
4  5505076  Trauma and organizations / edited by Earl Hopper.   

                                           thumbnail              Call_Number  
0  https://files.lib.byu.edu/search/thumbnails/ca...        BF 174 .J85 J2936  
1                                               None        BF 1583 .L44 1997  
2  https://www.syndetics.com/index.php?isbn=97814...       BF 76.5 .Q355 2012  
3                                               None               BF 636 .W6  
4  https://www.syndetics.com/index.php?isbn=97818...  BF 175.5 .P75 T73x 2012

In [5]:
# Drop any entries where call number = none
df = df.drop(df[df.Call_Number == "None"].index)

In [6]:
# Remove call numbers that are not BF's
remove_indicies = []

for i, row in df.iterrows():

    curr_num = row['Call_Number']
    #print(curr_num)

    if curr_num[0] + curr_num[1] != "BF":
        print("Non-BF Call Number found, removing from dataset")
        print(curr_num)
        remove_indicies.append(i)
    else: # Fix spacing of BF without space for regex standardization
        if curr_num[2] != " ":
            df.at[i, 'Call_Number'] = curr_num[:2] + " " + curr_num[2:]

df = df.drop(remove_indicies)

Non-BF Call Number found, removing from dataset
HD 38 .S386 1981
Non-BF Call Number found, removing from dataset
B 105 .R25 C44
Non-BF Call Number found, removing from dataset
170 Sm44L 1887
Non-BF Call Number found, removing from dataset
BD 236 .I42 1995
Non-BF Call Number found, removing from dataset
RB 127 .P85 1986
Non-BF Call Number found, removing from dataset
ND 1495 .P8 S95 2003
Non-BF Call Number found, removing from dataset
AC 1 .G72 1982 vol.53
Non-BF Call Number found, removing from dataset
HQ 1064 .U5 A643 1985
Non-BF Call Number found, removing from dataset
C197do
Non-BF Call Number found, removing from dataset
RA565 .E47
Non-BF Call Number found, removing from dataset
BX 8645.6 .T86 2005
Non-BF Call Number found, removing from dataset
AC 1 .G72 1982 vol.53
Non-BF Call Number found, removing from dataset
BL 1135 .P7 A22 1972 vol.1 pt.1
Non-BF Call Number found, removing from dataset
QL 750 .T562x
Non-BF Call Number found, removing from dataset
AC 1 .G72 1982 vol.53
Non-BF

In [7]:
print(len(df))

18835


In [8]:
# Ensure Cutter number is spaced 
for i, row in df.iterrows():
    curr_num = row['Call_Number']

    bf_split = curr_num.split(' ')[1]

    check_split = bf_split.split('.')

    # If len <= 1, ignore this entry
    if len(check_split) > 1:
        # Rewrite this entry to separate cutter number from this entry
        if check_split[1][0].isalpha():
            print("Found entry to change")
            print(curr_num)

            new_call = ""
            for j, split in enumerate(curr_num.split(' ')):
                if j == 0:
                    new_call += split + ' '
                elif j != 1:
                    new_call += ' ' + split
                else:
                    new_call += check_split[0] + ' .' + check_split[1]

            df.at[i, 'Call_Number'] = new_call

Found entry to change
BF 720.V57 H34
Found entry to change
BF 720.S63 I53
Found entry to change
BF 720.M68 E84 1992
Found entry to change
BF 109.F74 G76 1991
Found entry to change
BF 108.R8 B3
Found entry to change
BF 720.S48 R64
Found entry to change
BF 108.S65 K68 1984
Found entry to change
BF 789.D4 A58x
Found entry to change
BF 720.P37 E67
Found entry to change
BF 463.S64 K6x 1987
Found entry to change
BF 720.S63 S625
Found entry to change
BF 789.D4 S33 1986
Found entry to change
BF 720.C63 I53x
Found entry to change
BF 463.S64 G6713 1992
Found entry to change
BF 789.D5 S31x 1992
Found entry to change
BF 720.V57 B76
Found entry to change
BF 789.S6 A83 1982
Found entry to change
BF 456.R2 I54
Found entry to change
BF 720.M45 I54 1984
Found entry to change
BF 720.A92 N53 1985
Found entry to change
BF 456.R2 O77x
Found entry to change
BF 789.F5 S34 1975
Found entry to change
BF 456.R2 G63 v.1
Found entry to change
BF 789.S8 B37x
Found entry to change
BF 456.R2 P41981
Found entry to ch

In [50]:
# Hardcoded fix
for i, row in df.iterrows():
  if row['Call_Number'] == 'BF 724.55.C63 S73 1989':
    print("Trash")
    df.at[i, 'Call_Number'] = 'BF 724.55 .C63 S73 1989'

Trash


In [9]:
# Rewrite Call_Numbers to be just numeric value up to cutter number
for i, row in df.iterrows():
    curr_num = row['Call_Number']
    print(curr_num)

df.head()

BF 174 .J85 J2936
BF 1583 .L44 1997
BF 76.5 .Q355 2012
BF 636 .W6
BF 175.5 .P75 T73x 2012
BF 121 .N94 1991
BF 723 .I6 W5
BF 723 .P365 R56x 1986
BF 1598 .F58 H83 1988
BF 210 .S72x 1972
BF 723 .T53 K345 2004
BF 870 .F7x 1847
BF 711 .D4
BF 698.5 .P38 2004
BF 201 .U88 2004
BF 723 .S6 D86x 1988b
BF 323 .E8 R43 2004
BF 311 .A93
BF 713 .M332 2005
BF 319 .P68
BF 431 .L45x 1985
BF 176 .F86 1986
BF 637 .S8 T518 1986
BF 18.02 .H84 1990
BF 175 .B87x 2003
BF 1583 .W65 1995
BF 633 .M4
BF 632.5 .C37
BF 175 .B67x 1985
BF 1576 .H633x 1996
BF 723 .S62 J25 1983 vol.1
BF 210 .U846x 1993
BF 173 .F85 W8x 1985
BF 173 .H45x 1985
BF 121 .C58 1974
BF 713 .S84 1986
BF 710 .K53 1988
BF 431 .A579 1993
BF 698 .P47x
BF 431 .G244 1983
BF 378 .S54 B33 1986
BF 697 .H373x 1998
BF 311 .R535x 1998
BF 1325 .B48
BF 408 .G33 1993
BF 432 .C48 S28 1990
BF 637 .S4 S29x 1988
BF 311 .N487x 1992
BF 113 .S35x 1959
BF 325 .P68 1992
BF 173 .P7756 1992
BF 448 .P56 1993
BF 639 .G6
BF 295 .D75
BF 311 .M433 1984
BF 371 .K533 1984
BF 207 

titleId                                          fullTitle  \
0        2  Complex, archetype, symbol in the psychology o...   
1  5242885  Hexen- und Dämonenglaube im Lande Braunschweig...   
2  5505056  Qualitative strategies for ethnocultural resea...   
3  2228271  The art of persuading people, by James A. Wors...   
4  5505076  Trauma and organizations / edited by Earl Hopper.   

                                           thumbnail              Call_Number  
0  https://files.lib.byu.edu/search/thumbnails/ca...        BF 174 .J85 J2936  
1                                               None        BF 1583 .L44 1997  
2  https://www.syndetics.com/index.php?isbn=97814...       BF 76.5 .Q355 2012  
3                                               None               BF 636 .W6  
4  https://www.syndetics.com/index.php?isbn=97818...  BF 175.5 .P75 T73x 2012

## Create new columns of just call number and letter of author

In [10]:
for i, row in df.iterrows():
    full_call = row['Call_Number']
    call_split = full_call.split(' ')
    call_num = call_split[1]

    #print("Numberic call number: ", call_split[1])
    #print("Associated Letter: ", first_letter)

    first_letter = call_split[2][1]


    if not first_letter.isalpha():
        if i == 623:
            first_letter = "B"
        elif i == 1487:
            first_letter = "U"
        elif i == 5916:
            first_letter = "C"
        elif i == 6010:
            first_letter = "M"
        elif i == 7135:
            first_letter = "G"
        elif i == 7941:
            first_letter = "I"
        elif i == 8040:
            first_letter = "C"
        elif i == 8106:
            first_letter = "L"
        elif i == 10739:
            first_letter = "A"
            call_num = 87.7
        elif i == 11320:
            first_letter = "A"
            call_num = 87.7
        elif i == 12771:
            first_letter = "B"
        elif i == 21144:
            first_letter = "D"


    print("Numberic call number: ", call_num)
    print("Associated Letter: ", first_letter)

    df.at[i, 'Call_Numeric'] = call_num
    df.at[i, 'Call_Alpha'] = first_letter

df.head()


Numberic call number:  174
Associated Letter:  J
Numberic call number:  1583
Associated Letter:  L
Numberic call number:  76.5
Associated Letter:  Q
Numberic call number:  636
Associated Letter:  W
Numberic call number:  175.5
Associated Letter:  P
Numberic call number:  121
Associated Letter:  N
Numberic call number:  723
Associated Letter:  I
Numberic call number:  723
Associated Letter:  P
Numberic call number:  1598
Associated Letter:  F
Numberic call number:  210
Associated Letter:  S
Numberic call number:  723
Associated Letter:  T
Numberic call number:  870
Associated Letter:  F
Numberic call number:  711
Associated Letter:  D
Numberic call number:  698.5
Associated Letter:  P
Numberic call number:  201
Associated Letter:  U
Numberic call number:  723
Associated Letter:  S
Numberic call number:  323
Associated Letter:  E
Numberic call number:  311
Associated Letter:  A
Numberic call number:  713
Associated Letter:  M
Numberic call number:  319
Associated Letter:  P
Numberic call

titleId                                          fullTitle  \
0        2  Complex, archetype, symbol in the psychology o...   
1  5242885  Hexen- und Dämonenglaube im Lande Braunschweig...   
2  5505056  Qualitative strategies for ethnocultural resea...   
3  2228271  The art of persuading people, by James A. Wors...   
4  5505076  Trauma and organizations / edited by Earl Hopper.   

                                           thumbnail              Call_Number  \
0  https://files.lib.byu.edu/search/thumbnails/ca...        BF 174 .J85 J2936   
1                                               None        BF 1583 .L44 1997   
2  https://www.syndetics.com/index.php?isbn=97814...       BF 76.5 .Q355 2012   
3                                               None               BF 636 .W6   
4  https://www.syndetics.com/index.php?isbn=97818...  BF 175.5 .P75 T73x 2012   

  Call_Numeric Call_Alpha  
0          174          J  
1         1583          L  
2         76.5          Q  
3          636          W  
4        175.5          P

In [12]:
df.at[8280, 'Call_Alpha'] = 'A'

for i, row in df.iterrows():
    if df.at[i, 'Call_Numeric'] == '724.55.C63':
        df.at[i, 'Call_Numeric'] = 724.55
    df.at[i, 'Call_Numeric'] = float(df.at[i, 'Call_Numeric'])

In [13]:
df.head()

titleId                                          fullTitle  \
0        2  Complex, archetype, symbol in the psychology o...   
1  5242885  Hexen- und Dämonenglaube im Lande Braunschweig...   
2  5505056  Qualitative strategies for ethnocultural resea...   
3  2228271  The art of persuading people, by James A. Wors...   
4  5505076  Trauma and organizations / edited by Earl Hopper.   

                                           thumbnail              Call_Number  \
0  https://files.lib.byu.edu/search/thumbnails/ca...        BF 174 .J85 J2936   
1                                               None        BF 1583 .L44 1997   
2  https://www.syndetics.com/index.php?isbn=97814...       BF 76.5 .Q355 2012   
3                                               None               BF 636 .W6   
4  https://www.syndetics.com/index.php?isbn=97818...  BF 175.5 .P75 T73x 2012   

  Call_Numeric Call_Alpha  
0        174.0          J  
1       1583.0          L  
2         76.5          Q  
3        636.0          W  
4        175.5          P

In [14]:
for i, row in df.iterrows():
    title_split = row['fullTitle'].split('/')

    title =title_split[0]
    if len(title_split) >= 2:
        author = title_split[1]
    else:
        author = "N/A"

    df.at[i, 'Title'] = title
    df.at[i, 'Author'] = author

In [15]:
df.head()

titleId                                          fullTitle  \
0        2  Complex, archetype, symbol in the psychology o...   
1  5242885  Hexen- und Dämonenglaube im Lande Braunschweig...   
2  5505056  Qualitative strategies for ethnocultural resea...   
3  2228271  The art of persuading people, by James A. Wors...   
4  5505076  Trauma and organizations / edited by Earl Hopper.   

                                           thumbnail              Call_Number  \
0  https://files.lib.byu.edu/search/thumbnails/ca...        BF 174 .J85 J2936   
1                                               None        BF 1583 .L44 1997   
2  https://www.syndetics.com/index.php?isbn=97814...       BF 76.5 .Q355 2012   
3                                               None               BF 636 .W6   
4  https://www.syndetics.com/index.php?isbn=97818...  BF 175.5 .P75 T73x 2012   

  Call_Numeric Call_Alpha                                              Title  \
0        174.0          J  Complex, archetype, symbol in the psychology o...   
1       1583.0          L  Hexen- und Dämonenglaube im Lande Braunschweig...   
2         76.5          Q  Qualitative strategies for ethnocultural resea...   
3        636.0          W  The art of persuading people, by James A. Wors...   
4        175.5          P                          Trauma and organizations    

                                              Author  
0       Translated from the German by Ralph Manheim.  
1                                  Joachim Lehrmann.  
2   edited by Donna K. Nagata, Laura Kohn-Wood, a...  
3                                                N/A  
4                             edited by Earl Hopper.

In [16]:
print(len(df))

18835


In [19]:
import mysql.connector
import pandas as pd
import numpy as np

# Connect to MYSQL Database
mydb = mysql.connector.connect(
    host="localhost",
    user="root",
    password="Gksdnihon101!",
    database='library_books'
)

# Create Cursor
mycursor = mydb.cursor()

for i, row in df.iterrows():
    table_index = i
    title_id = row['titleId']

    title = row['Title']
    title =  title.replace("\"", "\\\"")

    r_type = "Print"
    author = row['Author']
    author = author.replace("\"", "\\\"")

    call_num = row['Call_Number']
    digit = row['Call_Numeric']
    alpha = row['Call_Alpha']
    thumbnail = row['thumbnail']




    sql = f"""INSERT INTO ala_last (
            TableIndex, TitleID, Title, Resource_Type, Author, Call_Number, Call_Digit, Call_Author, Thumbnail_Link)
            VALUES ({table_index}, {title_id}, "{title}","{r_type}", "{author}","{call_num}", {digit}, "{alpha}", "{thumbnail}")"""
    #num_added += 1

    print(sql)

    # Execute and commit
    mycursor.execute(sql)
    mydb.commit()

INSERT INTO ala_last (
            TableIndex, TitleID, Title, Resource_Type, Author, Call_Number, Call_Digit, Call_Author, Thumbnail_Link)
            VALUES (0, 2, "Complex, archetype, symbol in the psychology of C. G. Jung ","Print", " Translated from the German by Ralph Manheim.","BF 174 .J85 J2936", 174.0, "J", "https://files.lib.byu.edu/search/thumbnails/cat.2.jpg")
INSERT INTO ala_last (
            TableIndex, TitleID, Title, Resource_Type, Author, Call_Number, Call_Digit, Call_Author, Thumbnail_Link)
            VALUES (1, 5242885, "Hexen- und Dämonenglaube im Lande Braunschweig : die Geschichte einer Verfolgung unter regionalem Aspekt ","Print", " Joachim Lehrmann.","BF 1583 .L44 1997", 1583.0, "L", "None")
INSERT INTO ala_last (
            TableIndex, TitleID, Title, Resource_Type, Author, Call_Number, Call_Digit, Call_Author, Thumbnail_Link)
            VALUES (2, 5505056, "Qualitative strategies for ethnocultural research ","Print", " edited by Donna K. Nagata, Laura Kohn

In [ ]:
+----------------+---------------+------+-----+---------+-------+
| Field          | Type          | Null | Key | Default | Extra |
+----------------+---------------+------+-----+---------+-------+
| Tableindex     | int           | YES  |     | NULL    |       |
| TitleID        | int           | YES  |     | NULL    |       |
| Title          | varchar(2048) | YES  |     | NULL    |       |
| Resource_Type  | varchar(2048) | YES  |     | NULL    |       |
| Author         | varchar(2048) | YES  |     | NULL    |       |
| Call_Number    | varchar(255)  | YES  |     | NULL    |       |
| Call_Digit     | float         | YES  |     | NULL    |       |
| Call_Author    | varchar(4)    | YES  |     | NULL    |       |
| Thumbnail_Link | varchar(4098) | YES  |     | NULL    |       |
+----------------+---------------+------+-----+---------+-------+
